In [1]:
import pandas as pd
import backtrader as bt
from __future__ import absolute_import, division, print_function, unicode_literals

In [2]:
cerebro = bt.Cerebro()

print("Starting Portfolio Value: %.2f" % cerebro.broker.getvalue())

cerebro.run()

print("Final Portfolio Value: %.2f" % cerebro.broker.getvalue())

Starting Portfolio Value: 10000.00
Final Portfolio Value: 10000.00


In [3]:
df = pd.read_csv('/home/coder/ADC2025/history_price/usdchf.csv')
df['time'] = pd.to_datetime(df['time'])
time_max = df['time'].max()
time_min = df['time'].min()
print("最大 time:", time_max)
print("最小 time:", time_min)

最大 time: 2025-09-12 16:58:00
最小 time: 2000-05-30 17:23:00


In [4]:
class MartingaleStrategy(bt.Strategy):
    params = (
        ('stake', 50),  # 初始仓位更大
        ('max_martingale', 10),  # 允许更高的马丁次数
    )

    def __init__(self):
        self.order = None
        self.last_trade_won = True
        self.martingale_count = 0
        self.stake = self.p.stake

    def notify_order(self, order):
        if order.status in [order.Completed, order.Canceled, order.Margin]:
            self.order = None

    def next(self):
        print(f"next called, position size: {self.position.size}, order: {self.order}, close: {self.data.close[0]}")
        if self.order:
            return  # 等待订单完成

        if not self.position:
            # 初始开多仓，更激进策略用更大仓位
            self.order = self.buy(size=self.stake)
            print(f"Buy order placed, size: {self.stake}")
        else:
            # 更激进马丁：亏损时加倍且次数更多
            if self.data.close[0] < self.position.price:
                if self.martingale_count < self.p.max_martingale:
                    self.stake *= 2
                    self.order = self.buy(size=self.stake)
                    self.martingale_count += 1
                    print(f"Martingale buy, new stake: {self.stake}, count: {self.martingale_count}")
            else:
                # 盈利则恢复初始仓位
                self.stake = self.p.stake
                self.martingale_count = 0
                self.close()
                print("Position closed, reset stake and martingale count")

# 选取一段数据作为回测
start_date = '2017-01-01'
end_date = '2017-03-01'
df_bt = df[(df['time'] >= start_date) & (df['time'] <= end_date)].copy()

data_feed = bt.feeds.PandasData(
    dataname=df_bt,
    datetime='time',
    open='open',
    high='high',
    low='low',
    close='close',
    volume='volume',
    openinterest=None
)

cerebro = bt.Cerebro()
cerebro.addstrategy(MartingaleStrategy)
cerebro.adddata(data_feed)
cerebro.broker.setcash(10000.0)

print("Starting Portfolio Value: %.2f" % cerebro.broker.getvalue())
cerebro.run()
print("Final Portfolio Value: %.2f" % cerebro.broker.getvalue())

Starting Portfolio Value: 10000.00
next called, position size: 0, order: None, close: 1.01898
Buy order placed, size: 50
next called, position size: 50, order: None, close: 1.01898
Position closed, reset stake and martingale count
next called, position size: 0, order: None, close: 1.01896
Buy order placed, size: 50
next called, position size: 50, order: None, close: 1.01898
Position closed, reset stake and martingale count
next called, position size: 0, order: None, close: 1.01901
Buy order placed, size: 50
next called, position size: 50, order: None, close: 1.01898
Martingale buy, new stake: 100, count: 1
next called, position size: 150, order: None, close: 1.01854
Martingale buy, new stake: 200, count: 2
next called, position size: 350, order: None, close: 1.01846
Martingale buy, new stake: 400, count: 3
next called, position size: 750, order: None, close: 1.01844
Martingale buy, new stake: 800, count: 4
next called, position size: 1550, order: None, close: 1.01845
Martingale buy, ne

In [ ]:
import pandas as pd

# 获取交易记录
trades = []
for strat in cerebro.runstrats:
    # 处理 _tradespending（list）
    for trade in strat[0].broker._tradespending:
        if hasattr(trade, 'isclosed') and trade.isclosed:
            trades.append({
                'symbol': getattr(trade.data, '_name', ''),
                'cmd': 0 if getattr(trade, 'long', False) else 1,
                'volume': getattr(trade, 'size', 0),
                'open_time': trade.open_datetime().timestamp(),
                'open_price': getattr(trade, 'price', 0.0),
                'sl': getattr(trade, 'sl', 0.0),
                'tp': getattr(trade, 'tp', 0.0),
                'close_time': trade.close_datetime().timestamp(),
                'reason': getattr(trade, 'close_reason', ''),
                'commission': getattr(trade, 'commission', 0.0),
                'swaps': getattr(trade, 'pnlcomm', 0.0) - getattr(trade, 'pnl', 0.0),
                'close_price': getattr(trade, 'close_price', 0.0),
                'profit': getattr(trade, 'pnlcomm', 0.0),
            })
    # 处理 _trades（defaultdict，值为list）
    for trade_list in strat[0].broker._trades.values():
        for trade in trade_list:
            if hasattr(trade, 'isclosed') and trade.isclosed:
                trades.append({
                    'symbol': getattr(trade.data, '_name', ''),
                    'cmd': 0 if getattr(trade, 'long', False) else 1,
                    'volume': getattr(trade, 'size', 0),
                    'open_time': trade.open_datetime().timestamp(),
                    'open_price': getattr(trade, 'price', 0.0),
                    'sl': getattr(trade, 'sl', 0.0),
                    'tp': getattr(trade, 'tp', 0.0),
                    'close_time': trade.close_datetime().timestamp(),
                    'reason': getattr(trade, 'close_reason', ''),
                    'commission': getattr(trade, 'commission', 0.0),
                    'swaps': getattr(trade, 'pnlcomm', 0.0) - getattr(trade, 'pnl', 0.0),
                    'close_price': getattr(trade, 'close_price', 0.0),
                    'profit': getattr(trade, 'pnlcomm', 0.0),
                })

df_trades = pd.DataFrame(trades)
print(df_trades)

<IPython.core.display.Javascript object>

AttributeError: 'BackBroker' object has no attribute '_tradespending'